**Step 1: Setting Up ExecuTorch**

In [1]:
!pip install executorch
# Testing release candidate
# pip install --extra-index-url https://download.pytorch.org/whl/test/cpu executorch==0.6.0 torch==2.7.0 torchaudio==2.7.0 torchvision==0.22.0

In [2]:
# Installing dependencies for Llama
!pip install transformers accelerate sentencepiece huggingface_hub tiktoken torchtune tokenizers snakeviz lm_eval==0.4.5 blobfile

**Step 2. Download Llama 3.2 1B/3B models**

In [3]:
from huggingface_hub import login
login()

In [4]:
!huggingface-cli download meta-llama/Llama-3.2-1B-Instruct --local-dir /content/models/Llama-3.2-1B-Instruct --local-dir-use-symlinks False

/usr/local/lib/python3.11/dist-packages/huggingface_hub/commands/download.py:139: FutureWarning: Ignoring --local-dir-use-symlinks. Downloading to a local directory does not use symlinks anymore.
  warnings.warn(
Fetching 13 files:   0% 0/13 [00:00<?, ?it/s]Downloading 'LICENSE.txt' to '/content/models/Llama-3.2-1B-Instruct/.cache/huggingface/download/cyBuwAu93UXke23CJCWORBYR70A=.085b47c1575cb889b7024030e60b78f54f0b8c9e.incomplete'

LICENSE.txt: 100% 7.71k/7.71k [00:00<00:00, 30.6MB/s]
Download complete. Moving file to /content/models/Llama-3.2-1B-Instruct/LICENSE.txt

config.json: 100% 877/877 [00:00<00:00, 4.66MB/s]
Download complete. Moving file to /content/models/Llama-3.2-1B-Instruct/config.json

USE_POLICY.md: 100% 6.02k/6.02k [00:00<00:00, 31.1MB/s]
Download complete. Moving file to /content/models/Llama-3.2-1B-Instruct/USE_POLICY.md

README.md:   0% 0.00/41.7k [00:00<?, ?B/s]

README.md: 100% 41.7k/41.7k [00:00<00:00, 3.71MB/s]
Download complete. Moving file to /content/models/

**Step 3: Export to ExecuTorch**

In [10]:
!cd /content/; python -m executorch.examples.models.llama.export_llama \
  --model "llama3_2" \
  --checkpoint /content/models/Llama-3.2-1B-Instruct/original/consolidated.00.pth \
  --params /content/models/Llama-3.2-1B-Instruct/original/params.json \
  -kv \
  --use_sdpa_with_kv_cache \
  -X \
  -d bf16 \
  --metadata '{"get_bos_id":128000, "get_eos_ids":[128009, 128001]}' \
  --output_name="Llama-3.2-1B-Instruct.pte"

[INFO 2025-04-10 15:15:57,966 utils.py:162] NumExpr defaulting to 2 threads.
[INFO 2025-04-10 15:15:59,519 export_llama_lib.py:684] Applying quantizers: []
[INFO 2025-04-10 15:15:59,805 export_llama_lib.py:649] Checkpoint dtype: torch.bfloat16
[INFO 2025-04-10 15:15:59,806 quantized_kv_cache.py:277] Replacing KVCache with CustomKVCache. This modifies the model in place.
[INFO 2025-04-10 15:15:59,847 custom_ops.py:34] Looking for libcustom_ops_aot_lib.so in /usr/local/lib/python3.11/dist-packages/executorch/extension/llm/custom_ops
[INFO 2025-04-10 15:15:59,855 custom_ops.py:39] Loading custom ops library: /usr/local/lib/python3.11/dist-packages/executorch/extension/llm/custom_ops/libcustom_ops_aot_lib.so
[INFO 2025-04-10 15:15:59,875 builder.py:173] Model after source transforms: Transformer(
  (tok_embeddings): Embedding(128256, 2048)
  (rope): Rope(
    (apply_rotary_emb): RotaryEmbedding()
  )
  (layers): ModuleList(
    (0-15): 16 x TransformerBlock(
      (attention): AttentionMHA

In [11]:
!mv /content/Llama-3.2-1B-Instruct.pte /content/models/Llama-3.2-1B-Instruct/original/

**Step 4: Upload to HF**

In [12]:
!huggingface-cli upload executorch-community/Llama-3.2-1B-Instruct-ET /content/models/Llama-3.2-1B-Instruct/original/ --exclude="*.pth"

Consider using `hf_transfer` for faster uploads. This solution comes with some limitations. See https://huggingface.co/docs/huggingface_hub/hf_transfer for more details.
Start hashing 3 files.
Finished hashing 3 files.
Llama-3.2-1B-Instruct.pte: 100% 2.47G/2.47G [01:01<00:00, 40.4MB/s]
Removing 2 file(s) from commit that have not changed.
https://huggingface.co/executorch-community/Llama-3.2-1B-Instruct-ET/tree/main/.
